In [1]:
if True:
    import numpy as np
    import pandas as pd

    # Add lab library
    import sys
    sys.path.insert(0, '/home/trevormjs/Documents/Science/APL/Lab')

    #---------------------------------------------------------------------#
    #                        matplotlib plotting                          #
    #---------------------------------------------------------------------#
    import matplotlib.pyplot as plt
    import matplotlib as mpl
    from jupyterthemes import jtplot
    from Helper.plotting import my_graph
    # Edit the font, font size, and axes width
    # mpl.rcParams['font.family'] = 'Avenir'
    plt.rcParams['font.size'] = 24
    plt.rcParams['axes.linewidth'] = 2
    jtplot.style(theme='monokai', context='notebook', ticks=False, grid=False)

    #---------------------------------------------------------------------#
    #                           bokeh plotting                            #
    #---------------------------------------------------------------------#
    from bokeh.plotting import figure, show, output_notebook
    from bokeh.themes import Theme
    from bokeh.io import curdoc, export_png
    from bokeh.models import (Range1d, Label, ColumnDataSource, LabelSet,
                              Legend)
    from Helper.plotting import style
    output_notebook()
    # curdoc().theme = Theme(filename="../Helper/theme.yml")

    #---------------------------------------------------------------------#
    #                       error and unit handling                       #
    #---------------------------------------------------------------------#
    from uncertainties import ufloat
    import Helper.numbers as nu
    from Helper.record import Measurement, Unit

    %load_ext autoreload
    %autoreload 2

Loading BokehJS ...

In [2]:
from bokeh.palettes import Category20_4 as colors

In [3]:
from Helper.numbers import rising_edge

In [4]:
from scipy.interpolate import interp1d

In [5]:
def read_scope_csv(path, n_sigs = 1):
    ret = []
    for n in range(n_sigs):
        config = pd.read_csv(path, header=None, usecols=[1+6*n, 2+6*n]).loc[:2]
        config = [record_length, sample_interval, trigger_point] = [
            [float(val), unit] for val, unit in zip(config[1+6*n], config[2+6*n])]
        config= {
            'record_length': record_length,
            'sample_interval': sample_interval,
            'trigger_point': trigger_point
        }
        display(config)
        data = pd.read_csv(path, header = None, usecols=[3+6*n, 4+6*n])
        data.columns = ['ts', 'mV']
        ret.append([data, config])
    return ret

In [6]:
def clean_vis_9010_diff(pd1,
                        pd2,
                        first=False,
                        filt_type='fft',
                        filter_param=.25,
                        plot=True,
                        filename=''):
    fig = figure(height=400)
    if filt_type == 'fft':
        pd1_clean = pd.Series(nu.fft_filter(pd1.mV, filter_param))
        pd2_clean = pd.Series(nu.fft_filter(pd2.mV, filter_param))
    elif filt_type == 'avg':
        pd1_clean = pd.Series(nu.moving_avg_filter(pd1.mV, filter_param))
        pd2_clean = pd.Series(nu.moving_avg_filter(pd2.mV, filter_param))
    else:
        raise ValueError('No filter match')

    print('pd1 unfiltered ', end='')
    pd1_start, pd1_end = nu.rising_edge(pd1_clean, pd1.ts, first)[0]
    print('pd2 unfiltered ', end='')
    pd2_start, pd2_end = nu.rising_edge(pd2_clean, pd2.ts, first)[0]

    # timerange = [pd1_start-25, pd2_end + 150]
    # pd1_clean = pd1_clean[timerange[0]:timerange[1]]
    # pd2_clean = pd2_clean[timerange[0]:timerange[1]]

    # Zero time vector relative to pd1 peak start
    t = pd1.ts - pd1.ts[pd1_start]  # [timerange[0]:timerange[1]]
    t_interp = np.linspace(t.min(), t.max(), len(pd2_clean) * 16)

    interp1 = interp1d(t, pd1_clean, kind='cubic')
    pd1_clean = pd.Series(interp1(t_interp))

    interp2 = interp1d(t, pd2_clean, kind='cubic')
    pd2_clean = pd.Series(interp2(t_interp))

    t = t_interp * 1e9

    print('pd1 filtered ', end='')
    pd1_inds, pd1_90_10_inds = nu.rising_edge(pd1_clean, t, first)
    t -= t[pd1_inds[0]]

    print('pd2 filtered ', end='')
    pd2_inds, pd2_90_10_inds = nu.rising_edge(pd2_clean, t, first)

    small_t = t[pd1_inds[0] - 50:pd1_inds[0] +
                (pd1_inds[1] - pd1_inds[0]) * 2 + 100]
    small_pd1 = pd1_clean[pd1_inds[0] - 50:pd1_inds[0] +
                          (pd1_inds[1] - pd1_inds[0]) * 2 + 100]

    peaks, b, b = nu.peak(small_pd1, 1, 0, 0, 0)
    widths, _, _, _ = nu.peak_widths(
        small_pd1,
        peaks,
    )
    print('pd1 peak halfmax:', widths[0] * (t[1] - t[0]))

    #
    small_t = t[pd2_inds[0] - 50:pd2_inds[0] +
                (pd2_inds[1] - pd2_inds[0]) * 2 + 100]
    small_pd2 = pd2_clean[pd2_inds[0] - 50:pd2_inds[0] +
                          (pd2_inds[1] - pd2_inds[0]) * 2 + 100]

    peaks, b, b = nu.peak(small_pd2, 1, 0, 0, 0)
    widths, _, _, _ = nu.peak_widths(
        small_pd2,
        peaks,
    )
    print('pd2 peak halfmax:', widths[0] * (t[1] - t[0]))

    pd1 = fig.line(
        t[pd1_inds[0] - 100:pd2_inds[1] * 2],
        pd1_clean[pd1_inds[0] - 100:pd2_inds[1] * 2],
        line_width=4,
        #                    legend_label='PD1'
    )
    pd2 = fig.line(
        t[pd1_inds[0] - 100:pd2_inds[1] * 2],
        pd2_clean[pd1_inds[0] - 100:pd2_inds[1] * 2],
        line_width=4,
        #                    legend_label='PD2',
        color='red')

    #     fig.line(t[pd1_inds[0]:pd1_inds[1]], pd1_clean[pd1_inds[0]:pd1_inds[1]], color = 'red', alpha = 1)
    #     fig.line(t[pd2_inds[0]:pd2_inds[1]], pd2_clean[pd2_inds[0]:pd2_inds[1]], color = 'blue', alpha = 1)

    minmax = fig.scatter(
        t[pd1_inds],
        pd1_clean[pd1_inds],
        color='black',
        size = 15
        # legend_label='peak min/max'
    )
    ten_90 = fig.scatter(
        t[pd1_90_10_inds],
        pd1_clean[pd1_90_10_inds],
        color='grey',
        size = 15
        #                          legend_label='10-90 points'
    )
    minmax = fig.scatter(
        t[pd2_inds],
        pd2_clean[pd2_inds],
        color='black',
        size = 15
        #                          legend_label='peak min/max'
    )
    ten_90 = fig.scatter(
        t[pd2_90_10_inds],
        pd2_clean[pd2_90_10_inds],
        color='grey',
        size = 15
        #                          legend_label='10-90 points'
    )

    fig.x_range = Range1d(t[pd1_inds[0]] - .5, t[pd2_inds[1]] * 1.3)
    fig.y_range = Range1d(-.1*pd1_clean[pd1_inds[1]], pd1_clean[pd1_inds[1]] * 1.05)
    fig.add_layout(
        Legend(items=[("PD1", [pd1]), ("PD2", [pd2]),
                      ("10-90 points", [ten_90]), ("peak min/max", [minmax])],
               orientation='horizontal'), 'above')
    #     fig.add_layout(
    #         Legend(items=[("10-90 points", [ten_90]), ("peak min/max", [minmax])],
    #                orientation='horizontal'), 'above')
    if plot:
        show(fig)
    else:
        del fig
    if filename:
        style(fig)
        export_png(fig, filename=filename)

    return pd.DataFrame(
        {
            'start': t[[pd1_inds[0], pd2_inds[0]]],
            'end': t[[pd1_inds[1], pd2_inds[1]]],
            '10': t[[pd1_90_10_inds[0], pd2_90_10_inds[0]]],
            '90': t[[pd1_90_10_inds[1], pd2_90_10_inds[1]]]
        },
        index=['sig1', 'sig2'])

## Test Pulse, Scope, and Laser Diode

In [7]:
[[squares, squares_config]] = read_scope_csv('./Data/l4_A_1_data.csv')

{'record_length': [10000.0, 'Points'],
 'sample_interval': [3.99999989e-09, 's'],
 'trigger_point': [4640.00039, 'Samples']}

In [8]:
fig = figure()
fig.line(squares.ts, squares.mV)
show(fig)

In [9]:
approx_amplitude = squares.mV.max() - squares.mV.min()
fourier_coefs = np.fft.fft(squares.mV, n=len(squares)*16)
fourier_freqs = np.fft.fftfreq(
    len(squares.mV)*16, squares_config['sample_interval'][0]
)

pulse_frequency = fourier_freqs[
    10:len(fourier_freqs)//2][
    fourier_coefs[10:len(fourier_freqs)//2].argmax()
]

approx_amplitude, 'mV', pulse_frequency, 'Hz'

(5.5999997545, 'mV', 92187.50253515632, 'Hz')

In [10]:
fig = figure()
fig.line(fourier_freqs, np.abs(fourier_coefs))
show(fig)

## Initial Optics Setup

#### Failed Data

In [11]:
[[pd1, pd1_config], [pd2, pd2_config]] = read_scope_csv(
    './Data/l4_C_data.csv', 2)

fig = figure()
fig.line(pd1.ts, pd1.mV, legend_label='PD1')
fig.line(pd1.ts, pd2.mV, legend_label='PD2', color='red')
show(fig)

{'record_length': [10000.0, 'Points'],
 'sample_interval': [1.9999999e-09, 's'],
 'trigger_point': [5020.00004, 'Samples']}

{'record_length': [10000.0, 'Points'],
 'sample_interval': [1.9999999e-09, 's'],
 'trigger_point': [5020.00004, 'Samples']}

In [12]:
[[pd1, pd1_config], [pd2, pd2_config]] = read_scope_csv(
    './Data/l4_C_data3.csv', 2)

fig = figure()
fig.line(pd1.ts, pd1.mV, legend_label='PD1')
fig.line(pd1.ts, nu.fft_filter(pd2.mV, .17), legend_label='PD2', color='red')
show(fig)

{'record_length': [10000.0, 'Points'],
 'sample_interval': [2.0000000185e-10, 's'],
 'trigger_point': [4834.00032, 'Samples']}

{'record_length': [10000.0, 'Points'],
 'sample_interval': [2.0000000185e-10, 's'],
 'trigger_point': [4834.00032, 'Samples']}

### Loading Data

In [13]:
[[pd1, pd1_config], [pd2, pd2_config]] = read_scope_csv(
    './Data/l4_C_data4.csv', 2)

fig = figure()
fig.line(pd1.ts, pd1.mV, legend_label='PD1')
fig.line(pd1.ts, pd2.mV, legend_label='PD2', color='red')
show(fig)

{'record_length': [10000.0, 'Points'],
 'sample_interval': [2.0000000185e-10, 's'],
 'trigger_point': [4932.80043, 'Samples']}

{'record_length': [10000.0, 'Points'],
 'sample_interval': [2.0000000185e-10, 's'],
 'trigger_point': [4932.80043, 'Samples']}

In [14]:
[[pd1_cable, pd1_config], [pd2_cable, pd2_config]] = read_scope_csv(
    './Data/l4_C_c_data.csv', 2)

fig = figure()
fig.line(pd1_cable.ts, pd1_cable.mV, legend_label='PD1_cable')
fig.line(pd1_cable.ts, pd2_cable.mV, legend_label='PD2_cable', color='red')
show(fig)

{'record_length': [10000.0, 'Points'],
 'sample_interval': [2.0000000185e-10, 's'],
 'trigger_point': [4923.20015, 'Samples']}

{'record_length': [10000.0, 'Points'],
 'sample_interval': [2.0000000185e-10, 's'],
 'trigger_point': [4923.20015, 'Samples']}

### Rising Edge analysis

#### First pass

In [15]:
fig = figure()
"""
Create a time vector beginning at zero for alignment purposes.
"""
t = pd1.loc[pd1.ts >= 0, 'ts'] * 1e9
t.index = range(len(t))
"""
Filter all curves such that they are identical. This is really for
ease of processing but also because they really should be identical,
and any differences must represent some error.
"""
pd1_cable_clean = pd.Series(nu.fft_filter(pd1_cable.mV, .44))
pd2_cable_clean = pd.Series(nu.fft_filter(pd2_cable.mV, .34))

pd1_clean = pd.Series(nu.fft_filter(pd1.mV, .34))
pd2_clean = pd.Series(nu.fft_filter(pd2.mV, .34))
"""
Caclulate the indeces of the rising edge for all signals, and the
locations of 10% and 90%.
"""
pd1_cable_inds, pd1_cable_90_10_inds = rising_edge(pd1_cable_clean,
                                                   pd1_cable.ts)
pd1_inds, pd1_90_10_inds = rising_edge(pd1_clean, pd1_cable.ts)

pd2_cable_inds, pd2_cable_90_20_inds = rising_edge(pd2_cable_clean,
                                                   pd2_cable.ts)
pd2_inds, pd2_90_20_inds = rising_edge(pd2_clean, pd2_cable.ts)
"""
Align each PD1 curve to the beginning of its rising edge.
Align each PD2 curve to the beginning of the rising edge of
the corresponding PD1.
"""
zi_pd1_cable = pd1_cable_clean[pd1_cable_inds[0]:]
zi_pd1 = pd1_clean[pd1_inds[0]:]

zi_pd2_cable = pd2_cable_clean[pd1_cable_inds[0]:]
zi_pd2 = pd2_clean[pd1_inds[0]:]
"""
Normalize each signal on the scale [0, 1].
"""
zi_pd1_cable -= zi_pd1_cable.min()
zi_pd2_cable -= zi_pd2_cable.min()
zi_pd1_cable /= zi_pd1_cable.max()
zi_pd2_cable /= zi_pd2_cable.max()

zi_pd1 -= zi_pd1.min()
zi_pd2 -= zi_pd2.min()
zi_pd1 /= zi_pd1.max()
zi_pd2 /= zi_pd2.max()
"""
Plot each pair of PD1 and PD2 signals, and calculate
their locations of etc.
"""
results = {}
for sig, name, color in zip([zi_pd1_cable, zi_pd1, zi_pd2_cable, zi_pd2],
                            ['PD1_cable', 'PD1', 'PD2_cable', 'PD2'], colors):
    sig.index = range(len(sig))
    fig.line(t, sig[:len(t)], legend_label=name, color=color, line_width=1.6)
    times = rising_edge(sig[:len(t)], t)
    times = times[0] + times[1]
    results.update({name: [t[i] for i in times]})
fig.xaxis.axis_label = 'time (ns)'
fig.yaxis.axis_label = 'mV'
fig.x_range = Range1d(-.4, 30)
style(fig)
show(fig)
export_png(fig, filename='l4_A.png')
results = pd.DataFrame(results, index=['start', 'stop', '10', '90']).T

10-90 time 2.000000079649e-09
10-90 time 2.000000180569e-09
10-90 time 2.400000155e-09
10-90 time 1.999999718999999e-09
10-90 time 2.00000005299
10-90 time 2.0000000287189996
10-90 time 2.400000200000001
10-90 time 1.999999722


In [16]:
diffs = pd.DataFrame(results.T[['PD2_cable', 'PD2']].values -
                     results.T[['PD1_cable', 'PD1']].values,
                     index=results.columns,
                     columns=['cable_diff', 'no-cable_diff'])
(diffs.cable_diff-diffs['no-cable_diff']).mean(), (diffs.cable_diff-diffs['no-cable_diff']).std()

(5.10000017006775, 0.20000017053124855)

#### Second Pass

In [ ]:
res = clean_vis_9010_diff(pd1, pd2, filename = '../Images/l4_C_a.png')
res.iloc[1] - res.iloc[0]

pd1 unfiltered 10-90 time 2.0000000712810003e-09
pd2 unfiltered 10-90 time 2.2000001799999994e-09
pd1 filtered 10-90 time 2.1372996649880314
pd2 filtered 10-90 time 2.187294978788736
pd1 peak halfmax: 4.6573077059290116
pd2 peak halfmax: 4.534987707144018


In [ ]:
res2 = clean_vis_9010_diff(pd1_cable, pd2_cable, filename = '../Images/l4_C_a.png')
res1 = clean_vis_9010_diff(pd1, pd2, filename = '../Images/l4_C_b.png')
print('With extra cable time measurements')
print(np.round(res1, 2).to_latex())
print('Without extra cable time measurements')
print(np.round(res2, 2).to_latex())

In [ ]:
dif = pd.DataFrame([(res1.iloc[1] - res1.iloc[0]),
                    (res2.iloc[1] - res2.iloc[0])],
                   index=['Same Cable', 'Different Cable'])
print(pd.DataFrame([dif.mean(1), dif.std(1)], index = ['value','std']).T.to_latex())
difdif = dif.iloc[1] - dif.iloc[0]
difdif_val = ufloat(difdif.mean(), difdif.std())
'Added time due to the longer cable mean and standard deviation: ', nu.print_unc(difdif_val)

In [ ]:
cable_sol = 944.5e-3/difdif_val*10
nu.print_unc(cable_sol)[:2], '1e8 m/s'

In [ ]:
nu.print_unc(2.9979/cable_sol)[:2], 'effective refractive index'

## D

### Air

#### Setup Distances

In [ ]:
air_pd2_path = ufloat(917.5, .5) + ufloat(730.0, .5) + ufloat(124.5, .5)
air_pd1_path = ufloat(168.5, .5)
air_length_diff = air_pd2_path - air_pd1_path
air_length_diff *= 1e-3 # convert to meters
air_length_diff

#### Loading Data

In [ ]:
[[pd1_air, air_config], [pd2_air, air_config]] = read_scope_csv(
    './Data/l4_D_1_b.csv', 2)
pd1_air.loc[pd1_air.ts > 6e-9, 'mV'] = 0
pd2_air.loc[pd2_air.ts > 1.1e-8, 'mV'] = 0

fig = figure()

fig.line(pd1_air.ts, pd1_air.mV, legend_label='pd1_air')
fig.line(pd1_air.ts, pd2_air.mV, legend_label='pd2_air', color='red')
show(fig)

#### Time Shift

In [ ]:
error_opt = pd.DataFrame(columns=['param', 'mean', 'std'])
error_opt.param = np.arange(.05, .55, .02)


def fun(row):
    filter_param = row.param
    air_firstpeak_times = clean_vis_9010_diff(
        pd1_air, pd2_air, False, filter_param=filter_param, plot=False)
    firstpeak_air_vals = (
        air_firstpeak_times.iloc[1] - air_firstpeak_times.iloc[0])
    row[['mean', 'std']] = firstpeak_air_vals.mean(), firstpeak_air_vals.std()
    return row


error_opt = error_opt.apply(fun, axis=1)

error_opt

In [ ]:
air_firstpeak_times = clean_vis_9010_diff(
    pd1_air, pd2_air, False, filter_param=.51, plot=True, filename = '../Images/l4_D_a.png')
print(np.round(air_firstpeak_times, 2).to_latex())

In [ ]:
air_timeshift = error_opt.iloc[22, 1:]
air_timeshift = ufloat(air_timeshift['mean'], air_timeshift['std'])
nu.print_unc(air_timeshift)[:2], 'air timeshift in ns'

In [ ]:
air_sol = air_length_diff/air_timeshift
nu.print_unc(air_sol)[:2], '1e8 m/s air SoL'

#### Refractive Index

In [ ]:
nu.print_unc(.299792458/air_sol)[:2], 'air refractive index'

### Glass

#### Cable Length

In [ ]:
FO_legth = ufloat(2065.5, .5)*1e-3

#### Loading Data

In [ ]:
[[pd1_glass, glass_config], [pd2_glass, glass_config]] = read_scope_csv(
    './Data/l4_D_2_b.csv', 2)

fig = figure()
pd1_glass.loc[pd1_glass.ts > 6e-9, 'mV'] = 0
pd2_glass.loc[pd2_glass.ts > 2.1e-8, 'mV'] = 0
fig.line(pd1_glass.ts, pd1_glass.mV, legend_label='pd1_glass')
fig.line(pd1_glass.ts, pd2_glass.mV, legend_label='pd2_glass', color='red')
show(fig)

#### Timeshift

In [ ]:
glass_peak_times = clean_vis_9010_diff(pd1_glass, pd2_glass, False, 'fft', .6, filename = '../Images/l4_D_b.png')

print(np.round(glass_peak_times, 2).to_latex())
glass_timeshift = (glass_peak_times.iloc[1] - glass_peak_times.iloc[0])
glass_timeshift = ufloat(glass_timeshift.mean(), glass_timeshift.std())
nu.print_unc(glass_timeshift)[:2], 'ns glass time shift'

#### Refractive Index

In [ ]:
FO_shift = glass_timeshift - air_timeshift

In [ ]:
nu.print_unc(FO_shift)[:2], 'ns glass vs air time shift'

In [ ]:
glass_sol = FO_legth / FO_shift*10
nu.print_unc(glass_sol)[:2], '1e8 m/s SoL in FO cable'

In [ ]:
nu.print_unc(2.9979/glass_sol)[:2], 'refractive index of glass'

### Water

#### Water length

In [ ]:
water_length = ufloat(614.0, .5)*1e-3

#### Loading Data

In [ ]:
[[pd1_water, water_config], [pd2_water, water_config]] = read_scope_csv(
    './Data/l4_D_3_b.csv', 2)

pd1_water.loc[pd1_water.ts > 6e-9, 'mV'] = 0
pd2_water.loc[pd2_water.ts > 1.25e-8, 'mV'] = 0

fig = figure()
fig.line(pd1_water.ts, pd1_water.mV, legend_label='pd1_water')
fig.line(pd1_water.ts, pd2_water.mV, legend_label='pd2_water', color='red')
show(fig)

#### Time Shift

In [ ]:
water_peak_times = clean_vis_9010_diff(pd1_water, pd2_water, False, 'fft', 1.6, filename = '../Images/l4_D_c.png')

water_air_timeshift = (water_peak_times.iloc[1] - water_peak_times.iloc[0])
water_air_timeshift = ufloat(water_air_timeshift.mean(), water_air_timeshift.std())
water_air_timeshift

In [ ]:
print(np.round(water_peak_times, 2).to_latex())

In [ ]:
nu.print_unc(water_air_timeshift)[:2], 'ns air and water timeshift'

#### Refractive Index

$$T_A = time\ of\ flight\ diff\ air$$
$$T_W = time\ of\ flight\ in\ water$$
$$D_A = distance\ of\ air\ flight\ path$$
$$D_W = distance\ of\ water\ flight\ path$$
$$T_{A-W} = T_A \cdot \frac{D_A-D_W}{D_A}$$
$$T_W = T_A - T_{A-W}$$

In [ ]:
time_not_water = air_timeshift * (air_length_diff-2*water_length)/air_length_diff
water_timeshift = water_air_timeshift - time_not_water
print(nu.print_unc(water_timeshift)[:2], 'ns timeshift water only')

water_speed = 2*water_length/water_timeshift
print(nu.print_unc(water_speed*10)[:2], 'm/s SoL in water')
nu.print_unc(.29979/water_speed)[:2], 'refractive index of water'